In [1]:
addprocs(4)

4-element Array{Int64,1}:
 2
 3
 4
 5

## Defining +, *, - for SharedArray

In [2]:
import Base.+
function +(x::SharedArray, y::SharedArray)
    r = SharedArray(Float64, size(x)...)
    for i in eachindex(r)
        r[i] += x[i]+y[i]
    end
    r
end
import Base.*
function *(x::SharedArray, y::SharedArray)
    r = SharedArray(Float64, size(x, 1), size(y, 2))
    temp = x*sdata(y)
    for i in eachindex(r)
        r[i] = temp[i]
    end
    r
end
function *(A::SparseMatrixCSC, x::SharedArray)
    r = SharedArray(Float64, size(A, 1), size(x, 2))
    Ax = A*sdata(x)
    for i in eachindex(r)
        r[i] = Ax[i]
    end
    r
end   
function *(c::Float64, x::SharedArray)
    r = SharedArray(Float64, size(x)...)
    for i in eachindex(r)
        r[i] = c*x[i]
    end
    r
end
import Base.-
function -(x::SharedArray, y::SharedArray)
    r = SharedArray(Float64, size(x)...)
    for i in eachindex(r)
        r[i] += x[i]-y[i]
    end
    r
end

- (generic function with 191 methods)

In [3]:
f_function(x, y) = 5*pi^2*sin(pi*x)*cos(2*pi*y)
bnd_u(x, y) = sin(pi*x)*cos(2*pi*y)
function GS_ord(level, b, x, iter)
    length = 2^level-1
    h = 1/(2^level)
    n = length^2
    if level==1
        x[1] = (h^2)*b[1]/4
        return x
    end
    
    for count = 1:iter
        for i = 1:n
            temp = 0
            if (i%length != 1)
                temp += x[i-1]*(-h^(-2))
            end
            if (i%length != 0)
                temp += x[i+1]*(-h^(-2))
            end
            if(i > length)
                temp += x[i-length]*(-h^(-2))
            end
            if(i <= n-length)
                temp += x[i+length]*(-h^(-2))
            end
            x[i] = (h^2)*(b[i]-temp)/4
        end
    end
    x
end
function multiA(level, x)
    length = 2^level-1
    h = 1/(2^level)
    n = length^2
    temp = 4.0*x
    for i in 1:length, j in 1:length
        nd = (i-1)*length+j
        if i!=1
            temp[nd] -= x[nd-length]
        end
        if i!=length
            temp[nd] -= x[nd+length]
        end
        if j!=1
            temp[nd] -= x[nd-1]
        end
        if j!=length
            temp[nd] -= x[nd+1]
        end
        temp[nd] = temp[nd]/(h^2)
    end
    temp
end      
@everywhere function myrange(q::SharedArray)
    idx = indexpids(q)
    if idx == 0
        return 1:0, 1:0
    end
    nchunks = length(procs(q))
    splits = [round(Int, s) for s in linspace(0,round(Int, sqrt(size(q, 1))),nchunks+1)]
    1:round(Int, sqrt(size(q, 1))), splits[idx]+1:splits[idx+1]
end
@everywhere function myrange2(q::SharedArray)
    idx = indexpids(q)
    if idx == 0
        # This worker is not assigned a piece
        return 1:0, 1:0
    end
    nchunks = length(procs(q))
    splits = [round(Int, s) for s in linspace(0,round(Int, sqrt(size(q, 1))),nchunks+1)]
    splits[idx]+1:splits[idx+1], 1:round(Int, sqrt(size(q, 1)))
end
@everywhere function GS_chunk!(level, b, x, irange, jrange)
    #@show (irange, jrange)  # display so we can see what's happening
    h = 1/(2^level)
    length = 2^level-1
    for j in jrange, i in irange
        nd = (i-1)*length+j
        temp = 0
        if j!=1
            temp += x[nd-1]*(-h^(-2))
        end
        if j!=length
            temp += x[nd+1]*(-h^(-2))
        end
        if i!=1
            temp += x[nd-length]*(-h^(-2))
        end
        if i!=length
            temp += x[nd+length]*(-h^(-2))
        end
        x[nd] = (h^2)*(b[nd]-temp)/4     
    end
    x
end
@everywhere GS_shared_chunk!(level, b, x) = GS_chunk!(level, b, x, myrange(x)...)
@everywhere GS_shared_chunk2!(level, b, x) = GS_chunk!(level, b, x, myrange2(x)...)
function GS_v!(level, b, x, iter)
    @sync begin
        for i = 1:iter
            for p in procs(x)
                @async remotecall_wait(GS_shared_chunk!, p, level, b, x)
            end
        end
    end
    x
end
function GS_h!(level, b, x, iter)
    @sync begin
        for i = 1:iter
            for p in procs(x)
                @async remotecall_wait(GS_shared_chunk2!, p, level, b, x)
            end
        end
    end
    x
end
function GS_mix!(level, b, x, iter)
    @sync begin
        for i = 1:round(Int, iter/2)
            for p in procs(x)
                @async remotecall_wait(GS_shared_chunk!, p, level, b, x)
            end
            for p in procs(x)
                @async remotecall_wait(GS_shared_chunk2!, p, level, b, x)
            end                
        end
    end
    x
end

GS_mix! (generic function with 1 method)

In [4]:
@everywhere function Restriction_chunk!(level, x, Rx, irange, jrange)
    fine_length = 2^(level+1)-1
    coarse_length = 2^level-1
    for i in irange, j in jrange
        coarse_nd = (i-1)*coarse_length+j
        fine_nd = (2i-1)*fine_length+2j
        Rx[coarse_nd] += x[fine_nd]/4
        Rx[coarse_nd] += x[fine_nd+1]/8
        Rx[coarse_nd] += x[fine_nd-1]/8
        Rx[coarse_nd] += x[fine_nd+fine_length]/8
        Rx[coarse_nd] += x[fine_nd-fine_length]/8
        Rx[coarse_nd] += x[fine_nd+fine_length+1]/16
        Rx[coarse_nd] += x[fine_nd+fine_length-1]/16
        Rx[coarse_nd] += x[fine_nd-fine_length+1]/16
        Rx[coarse_nd] += x[fine_nd-fine_length-1]/16
    end
    Rx
end
@everywhere Restriction_shared_chunk!(level, x, Rx) = Restriction_chunk!(level, x, Rx, myrange(Rx)...)
function Restriction!(level, x)
    Rx = SharedArray(Float64, (2^level-1)^2)
    @sync begin
        for p in procs(Rx)
            @async remotecall_wait(Restriction_shared_chunk!, p, level, x, Rx)
        end
    end
    Rx
end
@everywhere function Prolongation_chunk!(level, x, Px, irange, jrange)
    fine_length = 2^level-1
    coarse_length = 2^(level-1)-1
    for i in irange, j in jrange
        coarse_nd = (i-1)*coarse_length+j
        fine_nd = (2i-1)*fine_length+2j
        Px[fine_nd] += x[coarse_nd]
        Px[fine_nd+1] += x[coarse_nd]/2
        Px[fine_nd-1] += x[coarse_nd]/2
        Px[fine_nd+fine_length] += x[coarse_nd]/2
        Px[fine_nd-fine_length] += x[coarse_nd]/2
        Px[fine_nd+fine_length+1] += x[coarse_nd]/4
        Px[fine_nd+fine_length-1] += x[coarse_nd]/4
        Px[fine_nd-fine_length+1] += x[coarse_nd]/4
        Px[fine_nd-fine_length-1] += x[coarse_nd]/4        
    end
    Px
end 
@everywhere Prolongation_shared_chunk!(level, x, Px) = Prolongation_chunk!(level, x, Px, myrange(x)...)
function Prolongation!(level, x)
    Px = SharedArray(Float64, (2^level-1)^2)
    @sync begin
        for p in procs(x)
            @async remotecall_wait(Prolongation_shared_chunk!, p, level, x, Px)
        end
    end
    Px
end

Prolongation! (generic function with 1 method)

In [5]:
function createR(max_level, min_level) 
    ## Returns restriction matrices, i.e. R[1] is (min_level+1)→(min_level) Restriction matrix
    ## Prolongation matrix P = transpose(4R)
    R = []
    for i = (min_level+1):max_level
        current_level = i
        current_length = 2^current_level-1
        next_level = i-1
        next_length = 2^next_level-1
        Rk = spzeros(next_length^2, current_length^2)
        for i in 1:next_length, j in 1:next_length
            next_nd = (i-1)*next_length+j
            fine_nd = (2i-1)*current_length+2j
            Rk[next_nd, fine_nd] += 1/4
            Rk[next_nd, fine_nd+1] += 1/8
            Rk[next_nd, fine_nd-1] += 1/8
            Rk[next_nd, fine_nd+current_length] += 1/8
            Rk[next_nd, fine_nd-current_length] += 1/8
            Rk[next_nd, fine_nd+current_length+1] += 1/16
            Rk[next_nd, fine_nd+current_length-1] += 1/16
            Rk[next_nd, fine_nd-current_length+1] += 1/16
            Rk[next_nd, fine_nd-current_length-1] += 1/16
        end
        push!(R, Rk)
    end
    R
end
function createA(max_level, min_level)
    ## Create A in Au = f (after max_level, Au = r)
    A = []
    for k = min_level:max_level
        length = 2^k-1
        hx = 1./(2^k)
        hy = 1./(2^k)
        Ak = spzeros(length^2, length^2)
        for i in 1:length, j in 1:length
            nd = (i-1)*length+j ## Translate (i, j) coordinate to node number in long vector
            Ak[nd, nd] += 2.*hx^(-2)+2.*hy^(-2)
            if i!=1
                Ak[nd, nd-length] += -hx^(-2)
            end
            if i!=length
                Ak[nd, nd+length] += -hx^(-2)
            end
            if j!=1
                Ak[nd, nd-1] += -hy^(-2)
            end
            if j!=length
                Ak[nd, nd+1] += -hy^(-2)
            end
        end
        push!(A, Ak)
    end
    A
end    
function createf(max_level, boundary_u, f_function)
    ## Create f for max_level
    length = 2^max_level-1
    hx = 1./(2^max_level)
    hy = 1./(2^max_level)
    f = SharedArray(Float64, length^2)  
    ## Adding boundary condition(Dirichlet) 
    for i in 1:length, j in 1:length
        nd = (i-1)*length+j
        f[nd] += f_function(i*hx, j*hy)
        if i==1
            f[nd] += boundary_u(0, j*hy)*(hx^(-2))
        end
        if i==length
            f[nd] += boundary_u(1, j*hy)*(hx^(-2))
        end
        if j==1
            f[nd] += boundary_u(i*hx, 0)*(hy^(-2))
        end
        if j==length
            f[nd] += boundary_u(i*hx, 1)*(hy^(-2))
        end
    end
    f
end

createf (generic function with 1 method)

# Initialization

In [25]:
initial_level = 12
bottom_level = 1

println("Initializing conditions....")
x_sol = zeros((2^initial_level-1)^2)
initial_length = 2^initial_level-1
hx = 2.0^(-initial_level)
hy = 2.0^(-initial_level)
for i in 1:initial_length, j in 1:initial_length
    nd = (i-1)*initial_length+j
    x_sol[nd] = bnd_u(i*hx, j*hy)
end

## Initializing Au = f on finest grid
## R = createR(initial_level, bottom_level)
println("Initializing f....")
f = createf(initial_level, bnd_u, f_function)
println("Complete")

Initializing conditions....
Initializing f....
Complete


# Multigrid - Parallel version

In [7]:
function multigrid_parallel_V(initial_level, bottom_level, f, numgs)
    x = []
    r = []
    push!(x, SharedArray(Float64, (2^initial_level-1)^2))
    GS_mix!(initial_level, f, x[1], numgs)
    r_temp = f-multiA(initial_level, x[1])

    ## Going down to Coarsest grid
    for level = (initial_level-1):-1:(bottom_level)
        ## For each step, we do 3 things.
        ## First, restrict r of previous(finer) grid into current grid
        ## Second, GS Ax = r. Third, compute r_new = r - Ax. 
        ## Below is the list of indices of x, A, R, r for each level.
        ## index for x = initial_level - level + 1
        ## index for r = intial_level - level   
        r_temp = Restriction!(level, r_temp)
        push!(r, r_temp)
        if level>6    
            x_temp = GS_mix!(level, r_temp, SharedArray(Float64, (2^level-1)^2), numgs)
        else
            x_temp = GS_ord(level, r_temp, SharedArray(Float64, (2^level-1)^2), numgs)
        end      
        push!(x, x_temp)
        r_temp = r_temp - multiA(level, x_temp)
        println("==== Going down ",level+1,"->",level," Complete ====")
    end

    ## Going up to Finest grid
    for level = (bottom_level+1):(initial_level-1)
        x_temp = Prolongation!(level, x[initial_level-level+2]) ## Uprising x from the level below
        x[initial_level-level+1] += x_temp
        if level>6
            GS_mix!(level, r[initial_level-level], x[initial_level-level+1], numgs)
        else
            x[initial_level-level+1] = GS_ord(level, r[initial_level-level], x[initial_level-level+1], numgs)
        end
        println("==== Going up ", level-1,"->",level, " Complete ====")
    end

    ## Final step
    x[1] = x[1] + Prolongation!(initial_level, x[2])
    x[1] = GS_mix!(initial_level, f, x[1], numgs)
    println("==== Going up ", initial_level-1,"->",initial_level, " Complete ====")
    x[1]
end

multigrid_parallel_V (generic function with 1 method)

In [19]:
@time result = multigrid_parallel_V(initial_level, bottom_level, f, 10);

==== Going down 10->9 Complete ====
==== Going down 9->8 Complete ====
==== Going down 8->7 Complete ====
==== Going down 7->6 Complete ====
==== Going down 6->5 Complete ====
==== Going down 5->4 Complete ====
==== Going down 4->3 Complete ====
==== Going down 3->2 Complete ====
==== Going down 2->1 Complete ====
==== Going up 1->2 Complete ====
==== Going up 2->3 Complete ====
==== Going up 3->4 Complete ====
==== Going up 4->5 Complete ====
==== Going up 5->6 Complete ====
==== Going up 6->7 Complete ====
==== Going up 7->8 Complete ====
==== Going up 8->9 Complete ====
==== Going up 9->10 Complete ====
  2.482385 seconds (1.37 M allocations: 27.925 MB, 0.31% gc time)


In [20]:
println("Max error : ",maximum(abs(result - x_sol)))
println("Error rate : ",norm(result-x_sol)/norm(x_sol))

Max error : 0.017637022286921433
Error rate : 0.016074373138031138


# W-cycle version (Parallel)

In [10]:
function multigrid_parallel_W(initial_level, bottom_level, f, numgs)
    x = []
    r = []

    push!(x, SharedArray(Float64, (2^initial_level-1)^2))
    GS_mix!(initial_level, f, x[1], numgs)
    r_temp = f-multiA(initial_level, x[1])
    
    ## Going down to Coarsest grid
    for level = (initial_level-1):-1:(bottom_level)
        ## For each step, we do 3 things.
        ## First, restrict r of previous(finer) grid into current grid
        ## Second, GS Ax = r. Third, compute r_new = r - Ax. 
        ## Below is the list of indices of x, A, R, r for each level.
        ## index for x = initial_level - level + 1
        ## index for r = intial_level - level   
        r_temp = Restriction!(level, r_temp)
        push!(r, r_temp)
        if level>6    
            x_temp = GS_mix!(level, r_temp, SharedArray(Float64, (2^level-1)^2), numgs)
        else
            x_temp = GS_ord(level, r_temp, SharedArray(Float64, (2^level-1)^2), numgs)
        end
        push!(x, x_temp)
        r_temp = r_temp - multiA(level, x_temp)
        println("==== Going down ",level+1,"->",level," Complete ====")
    end

    ## Going up to Finest grid
    for level = (bottom_level+1):(initial_level-1)
        x_temp = Prolongation!(level, x[initial_level-level+2]) ## Uprising x from the level below
        x[initial_level-level+1] += x_temp
        if level>6
                GS_mix!(level, r[initial_level-level], x[initial_level-level+1], numgs)
        else
            x[initial_level-level+1] = GS_ord(level, r[initial_level-level], x[initial_level-level+1], numgs)
        end
        println("==== Going up ", level-1,"->",level, " Complete ====")
    end

    ## Middle step
    x[1] += Prolongation!(initial_level, x[2])
    GS_mix!(initial_level, f, x[1], numgs)
    println("==== Going up ", initial_level-1,"->",initial_level, " Complete ====")
    println("==== V-cycle 1 complete ====")
    x = [x[1]]
    r = []
    r_temp = f-multiA(initial_level, x[1])
    
    ## Going down to Coarsest grid
    for level = (initial_level-1):-1:(bottom_level)
        ## For each step, we do 3 things.
        ## First, restrict r of previous(finer) grid into current grid
        ## Second, GS Ax = r. Third, compute r_new = r - Ax. 
        ## Below is the list of indices of x, A, R, r for each level.
        ## index for x = initial_level - level + 1
        ## index for r = intial_level - level   
        r_temp = Restriction!(level, r_temp)
        push!(r, r_temp)
        if level>6    
            x_temp = GS_mix!(level, r_temp, SharedArray(Float64, (2^level-1)^2), numgs)
        else
            x_temp = GS_ord(level, r_temp, SharedArray(Float64, (2^level-1)^2), numgs)
        end
        push!(x, x_temp)
        r_temp = r_temp - multiA(level, x_temp)
        println("==== Going down ",level+1,"->",level," Complete ====")
    end

    ## Going up to Finest grid
    for level = (bottom_level+1):(initial_level-1)
        x_temp = Prolongation!(level, x[initial_level-level+2]) ## Uprising x from the level below
        x[initial_level-level+1] += x_temp
        if level>6
            GS_mix!(level, r[initial_level-level], x[initial_level-level+1], numgs)
        else
            x[initial_level-level+1] = GS_ord(level, r[initial_level-level], x[initial_level-level+1], numgs)
        end
        println("==== Going up ", level-1,"->",level, " Complete ====")
    end

    ## Final step
    x[1] += Prolongation!(initial_level, x[2])
    GS_mix!(initial_level, f, x[1], numgs)
    println("==== Going up ", initial_level-1,"->",initial_level, " Complete ====")   
    x[1]
end

multigrid_parallel_W (generic function with 1 method)

In [26]:
@time result = multigrid_parallel_W(initial_level, bottom_level, f, 20);

==== Going down 12->11 Complete ====
==== Going down 11->10 Complete ====
==== Going down 10->9 Complete ====
==== Going down 9->8 Complete ====
==== Going down 8->7 Complete ====
==== Going down 7->6 Complete ====
==== Going down 6->5 Complete ====
==== Going down 5->4 Complete ====
==== Going down 4->3 Complete ====
==== Going down 3->2 Complete ====
==== Going down 2->1 Complete ====
==== Going up 1->2 Complete ====
==== Going up 2->3 Complete ====
==== Going up 3->4 Complete ====
==== Going up 4->5 Complete ====
==== Going up 5->6 Complete ====
==== Going up 6->7 Complete ====
==== Going up 7->8 Complete ====
==== Going up 8->9 Complete ====
==== Going up 9->10 Complete ====
==== Going up 10->11 Complete ====
==== Going up 11->12 Complete ====
==== V-cycle 1 complete ====
==== Going down 12->11 Complete ====
==== Going down 11->10 Complete ====
==== Going down 10->9 Complete ====
==== Going down 9->8 Complete ====
==== Going down 8->7 Complete ====
==== Going down 7->6 Complete ===

In [27]:
println("Max error : ",maximum(abs(result - x_sol)))
println("Error rate : ",norm(result-x_sol)/norm(x_sol))

Max error : 8.033702779774998e-5
Error rate : 6.901819007626444e-5
